## Creating a clean environment

Use the [`venv`](https://docs.python.org/3/library/venv.html) command to create a new environment called `wikipedia_scraper_env`.

Activate it.

You will find more info about virtual environments in the course content and on the web.

## API Scraping

### A simple API query
You will start with the basics: how to do a simple request to an [API endpoint](../../2.python/2.python_advanced/05.Scraping/5.apis.ipynb).

You will use the [requests](https://requests.readthedocs.io/en/latest/) external library through the `import` keyword.

NOTE: external libraries need to be installed first. Check their documentation.

Check the [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/) section of the Requests documentation to:
1. use the `get()` method to connect to this endpoint: https://country-leaders.onrender.com/status
2. check if the `status_code` is equal to 200, which means OK.
    * if OK, `print()` the `text`` of the response.
    * if not, `print()` the `status_code`. 

Here is the signification of [HTTP status codes](https://en.wikipedia.org/wiki/List_of_HTTP_status_codes).


In [ ]:
# import the requests library (1 line)
import requests
# assign the root url (without /status) to the root_url variable for ease of reference (1 line)
root_url = 'https://www.immoweb.be/nl'
# assign the /status endpoint to another variable called status_url (1 line)
status_url = 'https://country-leaders.onrender.com/status/'
# query the /status endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(status_url) #PLA :req is the response object
print(req)
print(req.text)
# check the status_code using a condition and print appropriate messages (4 lines)
if req.status_code == 200:
    print(req.text)
else :
    print(req.status_code)

: 

### Dealing with JSON

[JSON](https://quickref.me/json) is the preferred format to deal with data over the web. You cannot avoid it so you would better get acquainted.

Connect to another endpoint called `/countries` but this time the API will return data in the JSON format. Check what to do in the Requests [Quickstart](https://requests.readthedocs.io/en/latest/user/quickstart/).


In [ ]:
# Set the countries_url variable (1 line)
countries_url = 'https://country-leaders.onrender.com/countries/'
# query the /countries endpoint using the get() method and store it in the req variable (1 line)
req = requests.get(countries_url) 
# Get the JSON content and store it in the countries variable (1 line)
countries = req.json()
# display the request's status code and the countries variable (1 line)
print (req.status_code, countries)

### Cookies anyone?

It looks like the access to this API is restricted...
Query the `/cookie` endpoint and extract the appropriate field to access your cookie.

You will need to use this cookie in each of the following API requests.

In [ ]:
# Set the cookie_url variable (1 line)
cookie_url = 'https://country-leaders.onrender.com/cookie'
# Query the enpoint, set the cookies variable and display it (2 lines)
cookie = requests.get(cookie_url).cookies
print(cookie)

Try to query the countries endpoint using the cookie, save the output and print it.

In [ ]:
# query the /countries endpoint, assign the output to the countries variable (1 line)
countries = requests.get(countries_url, cookies=cookie).json()
# display the countries variable (1 line)
print(countries)

Chances are the cookie has expired... Thanksfully, you got a nice error message. For now, simply execute the last 2 cells quickly so you get a result.

### Getting the actual data from the API

Query the `/leaders` endpoint.

In [ ]:
# Set the leaders_url variable (1 line)
leaders_url = 'https://country-leaders.onrender.com/leaders'
# query the /leaders endpoint, assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url, cookies=cookie).json()
# display the leaders variable (1 line)
print(leaders)

It looks like this endpoint requires additional information in order to return its result. Check the API [*documentation*](https://country-leaders.onrender.com/docs) in your web browser.

Change the query to accept *parameters*. You should know where to find help by now.

In [ ]:
# query the /leaders endpoint using cookies and parameters (take any country in countries)
# assign the output to the leaders variable (1 line)
leaders = requests.get(leaders_url, params= {"country" : "us"} ,cookies=cookie).json()
print(leaders)


### A sneak peak at the data (finally)

Look inside a few examples. Notice the dictionary keys available for each entry. You have your first example of *structured data*. This data was sanitized for your benefit, meaning it is readily exploitable without modification.

You will also notice there is a Wikipedia link for each entry. You will need to extract additional information there. This will be a case of *semi-structured* data.

The /countries endpoint returns a `list` of several country codes.

You need to loop through this list and query the /leaders endpoint for each one. Save each `json` result in a dictionary called `leaders_per_country`.

In [ ]:
#save in dictionary
leaders_per_country = {}
# 4 lines
for country in countries:    
    leaders_per_country[country] = requests.get(leaders_url, params= {"country" : country} ,cookies=cookie).json()
# display the leaders variable (1 line)
print(leaders_per_country)

In [ ]:
# one line
#van maarten

for country in countries: 
    leaders_per_country.update({country: requests.get(leaders_url, cookies=cookie, params={"country": country}).json()})
print(leaders_per_country)

It is finally time to create a `get_leaders()` function for the above code. You will build on it later-on. This function takes no parameter. Inside it, you will need to:
1. define the urls
2. get the cookies
2. get the countries
3. loop over them and save their leaders in a dictionary
4. return the dictionary

In [ ]:
# < 15 lines
def get_leaders():
    #root_url = 'https://country-leaders.onrender.com'
    status_url = 'https://country-leaders.onrender.com/status/'
    cookie_url = 'https://country-leaders.onrender.com/cookie'
    leaders_url = 'https://country-leaders.onrender.com/leaders'
    cookie = requests.get(cookie_url).cookies
    countries = requests.get(countries_url, cookies=cookie).json()
    for country in countries: 
        leaders_per_country.update({country: requests.get(leaders_url, cookies=cookie, params={"country": country}).json()})
    return(leaders_per_country)

get_leaders()


Test your function, save the result in the `leaders_per_country` dictionary and check its ouput.

In [ ]:
# 2 lines
leaders_per_country = get_leaders()
print(leaders_per_country)

## Extracting data from Wikipedia

Query one of the leaders' Wikipedia urls and display its `text` (not JSON).

In [55]:
# 3 lines
wikipedia_url = 'https://en.wikipedia.org/wiki/Joe_Biden'
#'https://nl.wikipedia.org/wiki/Guy_Verhofstadt'

req = requests.get(wikipedia_url).text
print(req)


<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" lang="en" dir="ltr">
<head>
<meta charset="UTF-8">
<title>Joe Biden - Wikipedia</title>
<script>(function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature

Ouch! You get the raw HTML code of the webpage. If you try to deal with it without tools, you will be there all night. Instead, use the [beautiful soup 4](https://www.crummy.com/software/BeautifulSoup/bs4/doc/) *external* library. You will find more info about it [here](../../2.python/2.python_advanced/05.Scraping/1.beautifulsoup_basic.ipynb) and [here](../../2.python/2.python_advanced/05.Scraping/2.beautifulsoup_advanced.ipynb)

Using the Quickstart section, start by importing the library and loading the output of your `get_text()` function.

Use the `prettify()` function and print it to take a look. You will start the actual parsing in the next step.

In [81]:
# 3 lines
from bs4 import BeautifulSoup
soup = BeautifulSoup(req,'html.parser')
print(soup.prettify(formatter="html"))



<!DOCTYPE html>
<html class="client-nojs vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpref-1 vector-feature-limited-width-content-enabled vector-feature-custom-font-size-clientpref-1 vector-feature-appearance-pinned-clientpref-1 vector-feature-night-mode-enabled skin-theme-clientpref-day vector-toc-available" dir="ltr" lang="en">
 <head>
  <meta charset="utf-8"/>
  <title>
   Joe Biden - Wikipedia
  </title>
  <script>
   (function(){var className="client-js vector-feature-language-in-header-enabled vector-feature-language-in-main-page-header-disabled vector-feature-sticky-header-disabled vector-feature-page-tools-pinned-disabled vector-feature-toc-pinned-clientpref-1 vector-feature-main-menu-pinned-disabled vector-feature-limited-width-clientpr

That looks better but you need to extract the right part of the webpage: the text of the first paragraph.

It is a bit tricky because Wikipedia pages slightly differ in structure from one language to the next. We cannot simply get the text for the first HTML paragraph.

You will start by getting all the HTML paragraphs from the HTML source and saving them in the `paragraphs` variable.

Use the documentation or google the appropriate keywords.

In [88]:
# 2 lines
paragraphs = soup.find_all('p')
print (paragraphs)

[<p class="mw-empty-elt">
</p>, <p><b>Joseph Robinette Biden Jr.</b><sup class="reference" id="cite_ref-3"><a href="#cite_note-3"><span class="cite-bracket">[</span>b<span class="cite-bracket">]</span></a></sup> (born November 20, 1942) is an American politician who has been the 46th and current <a href="/wiki/President_of_the_United_States" title="President of the United States">president of the United States</a> since 2021. A member of the <a href="/wiki/Democratic_Party_(United_States)" title="Democratic Party (United States)">Democratic Party</a>, he served as the 47th <a class="mw-redirect" href="/wiki/Vice_president_of_the_United_States" title="Vice president of the United States">vice president</a> from 2009 to 2017 under President <a href="/wiki/Barack_Obama" title="Barack Obama">Barack Obama</a> and represented <a href="/wiki/Delaware" title="Delaware">Delaware</a> in the <a class="mw-redirect" href="/wiki/U.S._Senate" title="U.S. Senate">U.S. Senate</a> from 1973 to 2009.
</p

If you try different urls, you might find that the paragraph you want may be at a different index each time.

That is where you need to be clever and ask yourself what would be a reliable way to identify the right index ie. which string matches only the first paragraph whatever the language...

Spend a good 30 minutes on the problem and brainstorm with your fellow learners. If you come out empty handed, ask your coach.

1. Loop over the HTML paragraphs
2. When you have identified the correct one
  * store the [text](https://www.crummy.com/software/BeautifulSoup/bs4/doc/#output) inside the `first_paragraph` variable
  * exit the loop

In [89]:
# <10 lines
paragraphs = soup.find_all('p')
for paragraph in paragraphs:
    if paragraph.find('b'):
        first_paragraph = paragraph.text
        break
print (first_paragraph)


Joseph Robinette Biden Jr.[b] (born November 20, 1942) is an American politician who has been the 46th and current president of the United States since 2021. A member of the Democratic Party, he served as the 47th vice president from 2009 to 2017 under President Barack Obama and represented Delaware in the U.S. Senate from 1973 to 2009.



At this stage, you can create a function to maintain consistency in your code. We will give you its *skeleton*, you will copy the code you wrote and make it work inside a function.

Don't forget to test your function.

In [175]:
# 10 lines
def get_first_paragraph(wikipedia_url):
    paragraphs = soup.find_all('p')
    for paragraph in paragraphs:
        if paragraph.find('b'):
            first_paragraph = paragraph.text
            break  
    return (wikipedia_url,first_paragraph)

In [176]:
# Test: 3 lines
get_first_paragraph('https://en.wikipedia.org/wiki/Joe_Biden')
print (wikipedia_url)
print(first_paragraph)


https://en.wikipedia.org/wiki/Joe_Biden
Joseph Robinette Biden Jr.[b] (born November 20, 1942) is an American politician who has been the 46th and current president of the United States since 2021. A member of the Democratic Party, he served as the 47th vice president from 2009 to 2017 under President Barack Obama and represented Delaware in the U.S. Senate from 1973 to 2009.



### Regular expressions to the rescue

Now that you have extracted the content of the first paragraph, the only thing that remains to finish your Wikipedia scraper is to sanitize the output.

Indeed some Wikipedia references, HTML code, phonetic pronunciation etc. may linger. You might find *regular expressions* handy to get rid of them and obtain pristine text. You will find some useful documentation about regular expressions [here](../../2.python/2.python_advanced/03.Regex/regex.ipynb)

Once you have one of your regex working online, try it in the cell below. 

Hints: 
* Check the `sub()` method documentation.
* Make sure to test urls in different languages. Some may look good but other do not.

In [553]:
# 3 lines



Overwrite the `get_first_paragraph()` function by applying your regex to the first paragraph before returning it.

In [554]:
# 10 lines 

Come up with other regexes to capture other patterns and sanitize the outputs completely. Modify your `get_first_paragraph()` function accordingly.

In [555]:
# < 20 lines


## Putting it all together

Let's go back to your `get_leaders()` function and update it with an *inner* loop over each leader. You will query the url provided and extract the first paragraph using the `get_first_paragraph()` function you just finished. You will then update that `leader`'s dictionary and move on to the next one.

Notice, the rest of the code should not change since you modify the leader's data one by one.

In [7]:
# < 20 lines
import requests
from bs4 import BeautifulSoup


# 10 lines
def get_first_paragraph(wikipedia_url):
    req = requests.get(wikipedia_url).text
    soup = BeautifulSoup(req,'html.parser')
    paragraphs = soup.find_all('p')
    for paragraph in paragraphs:
        if paragraph.find('b'):
            first_paragraph = paragraph.text
            break  
    return first_paragraph

def get_leaders():
    countries_url = 'https://country-leaders.onrender.com/countries/'
    status_url = 'https://country-leaders.onrender.com/status/'
    cookie_url = 'https://country-leaders.onrender.com/cookie'
    leaders_url = 'https://country-leaders.onrender.com/leaders'
    cookie = requests.get(cookie_url).cookies
    countries = requests.get(countries_url, cookies=cookie).json()
    for country in countries:         
        leader = requests.get(leaders_url, cookies=cookie, params={"country": country}).json()        
        for i in leader:
            leader_url = i["wikipedia_url"]
            i["first paragraph" ] = get_first_paragraph(leader_url)

    return(leader)

get_leaders()





[{'id': 'Q23',
  'first_name': 'George',
  'last_name': 'Washington',
  'birth_date': '1732-02-22',
  'death_date': '1799-12-14',
  'place_of_birth': 'Westmoreland County',
  'wikipedia_url': 'https://en.wikipedia.org/wiki/George_Washington',
  'start_mandate': '1789-04-30',
  'end_mandate': '1797-03-04',
  'first paragraph': ('https://en.wikipedia.org/wiki/George_Washington',
   'George Washington (February 22, 1732\xa0– December 14, 1799) was an American Founding Father, politician, military officer, and farmer who served as the first president of the United States from 1789 to 1797. Appointed by the Second Continental Congress as commander of the Continental Army in 1775, Washington led Patriot forces to victory in the American Revolutionary War and then served as president of the Constitutional Convention in 1787, which drafted the current Constitution of the United States. Washington has thus become commonly known as the "Father of his Country".\n')},
 {'id': 'Q76',
  'first_name'

In [557]:
# Check the output of your function (2 lines)


Does the function crash in the middle of the loop? Chances are the cookies have expired while looping over the leaders.

Modify your function with an *exception* or check if the `status_code` is a cookie error. In either case, get new cookies and query the api again.

If your code did not crash,

In [558]:
# < 25 lines



Check the output of your function again.

In [559]:
# Check the output of your function (1 line)


Well done! It took a while however... Let's speed things up. The main *bottleneck* is the loop. We call on the Wikipedia website many times.

You will use the same *session* to call all the wikipedia pages. Check the *Advanced Usage* section of the Requests module's documentation.

Start by modifying the `get_first_paragraph()` function to accept a session parameter and adjust the `get()` method call.

In [560]:
# < 20 lines


Modify your `get_leaders()` function to make use of a single session for all the Wikipedia calls.
1. create a `Session` object outside of the loop over countries.
2. pass it to the `get_first_paragraph()` function as an argument.

In [561]:
# <25 lines


Test your new functions.



## Saving your hard work

The final step is to save the ``leaders_per_country`` dictionary in the `leaders.json` file using the [json](https://docs.python.org/3/library/json.html) module. Check out the `with` statement.

In [562]:
# 3 lines


Make sure the file can be read back. Write the code to read the file. And check the variables are the same.

In [563]:
# 3 lines


Make a function `save(leaders_per_country)` to call this code easily.

In [564]:
# 3 lines


In [565]:
# Call the function (1 line)


## Tidy things up in a stand-alone python script

Congratulations! You now have a working scraper! However, your code is scattered throughout this notebook along side the tutorials. Hardly production ready...

Copy and paste what you need in a separate `leaders_scraper.py` file.
Make sure it works by calling `python3 leaders_scraper.py`

## To go further

If you want to practice scraping, you can read this section and tackle the exercise.

You have noticed the API returns very partial results for country leaders. Many are missing. Overwrite the `get_leaders()` function to get its list from Wikipedia and extract their *personal details* from the frame on the side.

Good luck!